## Dependencies

In [ ]:
import pandas as pd
import numpy as np
import json
import re 
import sys
import itertools
from tqdm import tqdm

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.preprocessing import MinMaxScaler
import matplotlib.pyplot as plt


import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
from spotipy.oauth2 import SpotifyOAuth
import spotipy.util as util

import warnings
warnings.filterwarnings("ignore")
%matplotlib inline

## Preparing Spotify dataset

#### Song level data

In [ ]:
spotify_tracks_df = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\archive\\tracks.csv')

In [ ]:
spotify_tracks_df.shape[0]

586672

In [ ]:
spotify_tracks_df.head()

id                                 name  popularity  \
0  35iwgR4jXetI318WEWsa1Q                                Carve           6   
1  021ht4sdgPcrDgSk7JTbKY  Capítulo 2.16 - Banquero Anarquista           0   
2  07A5yehtSnoedViJAZkNnc   Vivo para Quererte - Remasterizado           0   
3  08FmqUhxtyLTn6pAh6bk45        El Prisionero - Remasterizado           0   
4  08y9GfoqCWfOGsKdwojr5e                  Lady of the Evening           0   

   duration_ms  explicit              artists                  id_artists  \
0       126903         0              ['Uli']  ['45tIt06XoI0Iio4LBEVpls']   
1        98200         0  ['Fernando Pessoa']  ['14jtPCOoNZwquk5wd9DxrY']   
2       181640         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
3       176907         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
4       163080         0      ['Dick Haymes']  ['3BiJGZsyX9sJchTqcSA7Su']   

  release_date  danceability  energy  key  loudness  mode  speechiness  \
0   1922-02-22         0.645  0.4450    0   -13.338     1       0.4510   
1   1922-06-01         0.695  0.2630    0   -22.136     1       0.9570   
2   1922-03-21         0.434  0.1770    1   -21.180     1       0.0512   
3   1922-03-21         0.321  0.0946    7   -27.961     1       0.0504   
4         1922         0.402  0.1580    3   -16.900     0       0.0390   

   acousticness  instrumentalness  liveness  valence    tempo  time_signature  
0         0.674            0.7440     0.151    0.127  104.851               3  
1         0.797            0.0000     0.148    0.655  102.009               1  
2         0.994            0.0218     0.212    0.457  130.418               5  
3         0.995            0.9180     0.104    0.397  169.980               3  
4         0.989            0.1300     0.311    0.196  103.220               4

### Artist level data

In [ ]:
spotify_artists_df = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\archive\\artists.csv')

In [ ]:
spotify_artists_df.shape[0]

1162095

In [ ]:
spotify_artists_df.head()

id  followers genres  \
0  0DheY5irMjBUeLybbCUEZ2        0.0     []   
1  0DlhY15l3wsrnlfGio2bjU        5.0     []   
2  0DmRESX2JknGPQyO15yxg7        0.0     []   
3  0DmhnbHjm1qw6NCYPeZNgJ        0.0     []   
4  0Dn11fWM7vHQ3rinvWEl4E        2.0     []   

                                             name  popularity  
0  Armid & Amir Zare Pashai feat. Sara Rouzbehani           0  
1                                     ปูนา ภาวิณี           0  
2                                           Sadaa           0  
3                                       Tra'gruda           0  
4                          Ioannis Panoutsopoulos           0

### Need to merge "genres" column into song level data such that we can use that info for each song when creating the playlist vector

In [ ]:
spotify_artists_df.dtypes

id             object
followers     float64
genres         object
name           object
popularity      int64
dtype: object

#### Removing list type for genre and artists columns

In [ ]:
spotify_artists_df['genres'].values[45]

"['carnaval cadiz']"

In [ ]:
spotify_artists_df['genres'].values[45][0]

'['

In [ ]:
spotify_artists_df['genres_upd'] = spotify_artists_df['genres'].apply(lambda x: [re.sub(' ','_',i) for i in re.findall(r"'([^']*)'", x)])

In [ ]:
spotify_artists_df['genres_upd'].values[45][0]

'carnaval_cadiz'

In [ ]:
spotify_tracks_df['artists_upd_v1'] = spotify_tracks_df['artists'].apply(lambda x: re.findall(r"'([^']*)'", x))
spotify_tracks_df['artists_upd_v2'] = spotify_tracks_df['artists'].apply(lambda x: re.findall('\"(.*?)\"',x))
spotify_tracks_df['artists_upd'] = np.where(spotify_tracks_df['artists_upd_v1'].apply(lambda x: not x), spotify_tracks_df['artists_upd_v2'], spotify_tracks_df['artists_upd_v1'] )

In [ ]:
spotify_tracks_df.head()

id                                 name  popularity  \
0  35iwgR4jXetI318WEWsa1Q                                Carve           6   
1  021ht4sdgPcrDgSk7JTbKY  Capítulo 2.16 - Banquero Anarquista           0   
2  07A5yehtSnoedViJAZkNnc   Vivo para Quererte - Remasterizado           0   
3  08FmqUhxtyLTn6pAh6bk45        El Prisionero - Remasterizado           0   
4  08y9GfoqCWfOGsKdwojr5e                  Lady of the Evening           0   

   duration_ms  explicit              artists                  id_artists  \
0       126903         0              ['Uli']  ['45tIt06XoI0Iio4LBEVpls']   
1        98200         0  ['Fernando Pessoa']  ['14jtPCOoNZwquk5wd9DxrY']   
2       181640         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
3       176907         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
4       163080         0      ['Dick Haymes']  ['3BiJGZsyX9sJchTqcSA7Su']   

  release_date  danceability  energy  ...  speechiness  acousticness  \
0   1922-02-22         0.645  0.4450  ...       0.4510         0.674   
1   1922-06-01         0.695  0.2630  ...       0.9570         0.797   
2   1922-03-21         0.434  0.1770  ...       0.0512         0.994   
3   1922-03-21         0.321  0.0946  ...       0.0504         0.995   
4         1922         0.402  0.1580  ...       0.0390         0.989   

   instrumentalness  liveness  valence    tempo  time_signature  \
0            0.7440     0.151    0.127  104.851               3   
1            0.0000     0.148    0.655  102.009               1   
2            0.0218     0.212    0.457  130.418               5   
3            0.9180     0.104    0.397  169.980               3   
4            0.1300     0.311    0.196  103.220               4   

      artists_upd_v1  artists_upd_v2        artists_upd  
0              [Uli]              []              [Uli]  
1  [Fernando Pessoa]              []  [Fernando Pessoa]  
2  [Ignacio Corsini]              []  [Ignacio Corsini]  
3  [Ignacio Corsini]              []  [Ignacio Corsini]  
4      [Dick Haymes]              []      [Dick Haymes]  

[5 rows x 23 columns]

In [ ]:
spotify_tracks_df[spotify_tracks_df['name']=='Adore You']

id       name  popularity  duration_ms  explicit  \
86217  5AnCLGg35ziFOloEnXK4uu  Adore You          71       278747         0   
91884  3jjujdWJ72nww5eGnfs2E7  Adore You          88       207133         0   
92524  1M4qEo4HE3PRaCOM7EXNJq  Adore You          74       207133         0   

                artists                  id_artists release_date  \
86217   ['Miley Cyrus']  ['5YGY8feqx7naU7z4HrwZM6']   2013-10-04   
91884  ['Harry Styles']  ['6KImCVD70vtIoJWnq6nGn3']   2019-12-13   
92524  ['Harry Styles']  ['6KImCVD70vtIoJWnq6nGn3']   2019-12-06   

       danceability  energy  ...  speechiness  acousticness  instrumentalness  \
86217         0.583   0.655  ...       0.0315        0.1110          0.000004   
91884         0.676   0.771  ...       0.0483        0.0237          0.000007   
92524         0.676   0.771  ...       0.0483        0.0237          0.000007   

       liveness  valence    tempo  time_signature  artists_upd_v1  \
86217     0.113    0.201  119.759               4   [Miley Cyrus]   
91884     0.102    0.569   99.048               4  [Harry Styles]   
92524     0.102    0.569   99.048               4  [Harry Styles]   

       artists_upd_v2     artists_upd  
86217              []   [Miley Cyrus]  
91884              []  [Harry Styles]  
92524              []  [Harry Styles]  

[3 rows x 23 columns]

### We can see there are duplicate songs with different id's. Lets create our own identifier to remove duplicates.

In [ ]:
spotify_tracks_df['artists_song'] = spotify_tracks_df.apply(lambda row: str(row['artists_upd'][0])+str(row['name']),axis = 1)
spotify_tracks_df.drop_duplicates('artists_song',inplace = True)

In [ ]:
spotify_tracks_df[spotify_tracks_df['name']=='Adore You']

id       name  popularity  duration_ms  explicit  \
86217  5AnCLGg35ziFOloEnXK4uu  Adore You          71       278747         0   
91884  3jjujdWJ72nww5eGnfs2E7  Adore You          88       207133         0   

                artists                  id_artists release_date  \
86217   ['Miley Cyrus']  ['5YGY8feqx7naU7z4HrwZM6']   2013-10-04   
91884  ['Harry Styles']  ['6KImCVD70vtIoJWnq6nGn3']   2019-12-13   

       danceability  energy  ...  acousticness  instrumentalness  liveness  \
86217         0.583   0.655  ...        0.1110          0.000004     0.113   
91884         0.676   0.771  ...        0.0237          0.000007     0.102   

       valence    tempo  time_signature  artists_upd_v1  artists_upd_v2  \
86217    0.201  119.759               4   [Miley Cyrus]              []   
91884    0.569   99.048               4  [Harry Styles]              []   

          artists_upd           artists_song  
86217   [Miley Cyrus]   Miley CyrusAdore You  
91884  [Harry Styles]  Harry StylesAdore You  

[2 rows x 24 columns]

In [ ]:
spotify_tracks_df.head()

id                                 name  popularity  \
0  35iwgR4jXetI318WEWsa1Q                                Carve           6   
1  021ht4sdgPcrDgSk7JTbKY  Capítulo 2.16 - Banquero Anarquista           0   
2  07A5yehtSnoedViJAZkNnc   Vivo para Quererte - Remasterizado           0   
3  08FmqUhxtyLTn6pAh6bk45        El Prisionero - Remasterizado           0   
4  08y9GfoqCWfOGsKdwojr5e                  Lady of the Evening           0   

   duration_ms  explicit              artists                  id_artists  \
0       126903         0              ['Uli']  ['45tIt06XoI0Iio4LBEVpls']   
1        98200         0  ['Fernando Pessoa']  ['14jtPCOoNZwquk5wd9DxrY']   
2       181640         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
3       176907         0  ['Ignacio Corsini']  ['5LiOoJbxVSAMkBS2fUm3X2']   
4       163080         0      ['Dick Haymes']  ['3BiJGZsyX9sJchTqcSA7Su']   

  release_date  danceability  energy  ...  acousticness  instrumentalness  \
0   1922-02-22         0.645  0.4450  ...         0.674            0.7440   
1   1922-06-01         0.695  0.2630  ...         0.797            0.0000   
2   1922-03-21         0.434  0.1770  ...         0.994            0.0218   
3   1922-03-21         0.321  0.0946  ...         0.995            0.9180   
4         1922         0.402  0.1580  ...         0.989            0.1300   

   liveness  valence    tempo  time_signature     artists_upd_v1  \
0     0.151    0.127  104.851               3              [Uli]   
1     0.148    0.655  102.009               1  [Fernando Pessoa]   
2     0.212    0.457  130.418               5  [Ignacio Corsini]   
3     0.104    0.397  169.980               3  [Ignacio Corsini]   
4     0.311    0.196  103.220               4      [Dick Haymes]   

   artists_upd_v2        artists_upd  \
0              []              [Uli]   
1              []  [Fernando Pessoa]   
2              []  [Ignacio Corsini]   
3              []  [Ignacio Corsini]   
4              []      [Dick Haymes]   

                                        artists_song  
0                                           UliCarve  
1  Fernando PessoaCapítulo 2.16 - Banquero Anarqu...  
2  Ignacio CorsiniVivo para Quererte - Remasterizado  
3       Ignacio CorsiniEl Prisionero - Remasterizado  
4                     Dick HaymesLady of the Evening  

[5 rows x 24 columns]

In [ ]:
spotify_artists_df.rename(columns = {'id':'id_artists'}, inplace = True)

In [ ]:
spotify_artists_df.head()

id_artists  followers genres  \
0  0DheY5irMjBUeLybbCUEZ2        0.0     []   
1  0DlhY15l3wsrnlfGio2bjU        5.0     []   
2  0DmRESX2JknGPQyO15yxg7        0.0     []   
3  0DmhnbHjm1qw6NCYPeZNgJ        0.0     []   
4  0Dn11fWM7vHQ3rinvWEl4E        2.0     []   

                                             name  popularity genres_upd  
0  Armid & Amir Zare Pashai feat. Sara Rouzbehani           0         []  
1                                     ปูนา ภาวิณี           0         []  
2                                           Sadaa           0         []  
3                                       Tra'gruda           0         []  
4                          Ioannis Panoutsopoulos           0         []

In [ ]:
spotify_tracks_df['id_artists'] = spotify_tracks_df['id_artists'].apply(lambda x: re.findall(r"'([^']*)'", x))

In [ ]:
spotify_tracks_df.head()

id                                 name  popularity  \
0  35iwgR4jXetI318WEWsa1Q                                Carve           6   
1  021ht4sdgPcrDgSk7JTbKY  Capítulo 2.16 - Banquero Anarquista           0   
2  07A5yehtSnoedViJAZkNnc   Vivo para Quererte - Remasterizado           0   
3  08FmqUhxtyLTn6pAh6bk45        El Prisionero - Remasterizado           0   
4  08y9GfoqCWfOGsKdwojr5e                  Lady of the Evening           0   

   duration_ms  explicit              artists                id_artists  \
0       126903         0              ['Uli']  [45tIt06XoI0Iio4LBEVpls]   
1        98200         0  ['Fernando Pessoa']  [14jtPCOoNZwquk5wd9DxrY]   
2       181640         0  ['Ignacio Corsini']  [5LiOoJbxVSAMkBS2fUm3X2]   
3       176907         0  ['Ignacio Corsini']  [5LiOoJbxVSAMkBS2fUm3X2]   
4       163080         0      ['Dick Haymes']  [3BiJGZsyX9sJchTqcSA7Su]   

  release_date  danceability  energy  ...  acousticness  instrumentalness  \
0   1922-02-22         0.645  0.4450  ...         0.674            0.7440   
1   1922-06-01         0.695  0.2630  ...         0.797            0.0000   
2   1922-03-21         0.434  0.1770  ...         0.994            0.0218   
3   1922-03-21         0.321  0.0946  ...         0.995            0.9180   
4         1922         0.402  0.1580  ...         0.989            0.1300   

   liveness  valence    tempo  time_signature     artists_upd_v1  \
0     0.151    0.127  104.851               3              [Uli]   
1     0.148    0.655  102.009               1  [Fernando Pessoa]   
2     0.212    0.457  130.418               5  [Ignacio Corsini]   
3     0.104    0.397  169.980               3  [Ignacio Corsini]   
4     0.311    0.196  103.220               4      [Dick Haymes]   

   artists_upd_v2        artists_upd  \
0              []              [Uli]   
1              []  [Fernando Pessoa]   
2              []  [Ignacio Corsini]   
3              []  [Ignacio Corsini]   
4              []      [Dick Haymes]   

                                        artists_song  
0                                           UliCarve  
1  Fernando PessoaCapítulo 2.16 - Banquero Anarqu...  
2  Ignacio CorsiniVivo para Quererte - Remasterizado  
3       Ignacio CorsiniEl Prisionero - Remasterizado  
4                     Dick HaymesLady of the Evening  

[5 rows x 24 columns]

In [ ]:
spotify_tracks_df = spotify_tracks_df.reset_index(drop=True)

In [ ]:
for i in tqdm(range(len(spotify_tracks_df))):
    spotify_tracks_df['id_artists'][i] = spotify_tracks_df['id_artists'][i][0]

100%|█████████████████████████████████████████████████████████████████████████| 523475/523475 [42:29<00:00, 205.33it/s]


In [ ]:
spotify_tracks_df

id                                 name  \
0       35iwgR4jXetI318WEWsa1Q                                Carve   
1       021ht4sdgPcrDgSk7JTbKY  Capítulo 2.16 - Banquero Anarquista   
2       07A5yehtSnoedViJAZkNnc   Vivo para Quererte - Remasterizado   
3       08FmqUhxtyLTn6pAh6bk45        El Prisionero - Remasterizado   
4       08y9GfoqCWfOGsKdwojr5e                  Lady of the Evening   
...                        ...                                  ...   
523470  1ZwZsVZUiyFwIHMNpI3ERt                           Skyscraper   
523471  5rgu12WBIHQtvej2MdHSH0                                  云与海   
523472  0NuWgxEp51CutD2pJoF4OM                                blind   
523473  27Y1N4Q4U3EfDU5Ubw8ws2            What They'll Say About Us   
523474  45XJsGpFTyzbzeWK8VzR8S                      A Day At A Time   

        popularity  duration_ms  explicit                          artists  \
0                6       126903         0                          ['Uli']   
1                0        98200         0              ['Fernando Pessoa']   
2                0       181640         0              ['Ignacio Corsini']   
3                0       176907         0              ['Ignacio Corsini']   
4                0       163080         0                  ['Dick Haymes']   
...            ...          ...       ...                              ...   
523470           4       106002         0                  ['Emilie Chin']   
523471          50       258267         0                      ['阿YueYue']   
523472          72       153293         0                   ['ROLE MODEL']   
523473          70       187601         0                      ['FINNEAS']   
523474          58       142003         0  ['Gentle Bones', 'Clara Benin']   

                    id_artists release_date  danceability  energy  ...  \
0       45tIt06XoI0Iio4LBEVpls   1922-02-22         0.645  0.4450  ...   
1       14jtPCOoNZwquk5wd9DxrY   1922-06-01         0.695  0.2630  ...   
2       5LiOoJbxVSAMkBS2fUm3X2   1922-03-21         0.434  0.1770  ...   
3       5LiOoJbxVSAMkBS2fUm3X2   1922-03-21         0.321  0.0946  ...   
4       3BiJGZsyX9sJchTqcSA7Su         1922         0.402  0.1580  ...   
...                        ...          ...           ...     ...  ...   
523470  4USdOnfLczwUglA3TrdHs2   2020-02-08         0.626  0.5300  ...   
523471  1QLBXKM5GCpyQQSVMNZqrZ   2020-09-26         0.560  0.5180  ...   
523472  1dy5WNgIKQU6ezkpZs4y8z   2020-10-21         0.765  0.6630  ...   
523473  37M5pPGs6V1fchFJSgCguX   2020-09-02         0.535  0.3140  ...   
523474  4jGPdu95icCKVF31CcFKbS   2021-03-05         0.696  0.6150  ...   

        acousticness  instrumentalness  liveness  valence    tempo  \
0              0.674          0.744000    0.1510   0.1270  104.851   
1              0.797          0.000000    0.1480   0.6550  102.009   
2              0.994          0.021800    0.2120   0.4570  130.418   
3              0.995          0.918000    0.1040   0.3970  169.980   
4              0.989          0.130000    0.3110   0.1960  103.220   
...              ...               ...       ...      ...      ...   
523470         0.113          0.856000    0.1040   0.2150  120.113   
523471         0.785          0.000000    0.0648   0.2110  131.896   
523472         0.141          0.000297    0.0924   0.6860  150.091   
523473         0.895          0.000150    0.0874   0.0663  145.095   
523474         0.206          0.000003    0.3050   0.4380   90.029   

        time_signature               artists_upd_v1  artists_upd_v2  \
0                    3                        [Uli]              []   
1                    1            [Fernando Pessoa]              []   
2                    5            [Ignacio Corsini]              []   
3                    3            [Ignacio Corsini]              []   
4                    4                [Dick Haymes]              []   
...                ...                          ...             ...   
523470     

In [ ]:
spotify_complete_df = spotify_tracks_df.merge(spotify_artists_df, how = 'inner', on = 'id_artists')

In [ ]:
spotify_complete_df

id             name_x  popularity_x  duration_ms  \
0       35iwgR4jXetI318WEWsa1Q              Carve             6       126903   
1       0PH9AACae1f957JAavhOl2           Lazy Boi             0       157333   
2       2SiNuAZ6jIU9xhClRKXcST             Sketch             0        87040   
3       4vV7uBcF2AnjNTOejBS5oL            L'enfer             0        40000   
4       598LlBn6jpEpVbLjmZPsYV           Graphite             0       104400   
...                        ...                ...           ...          ...   
511995  0MmaEacabpK8Yp3Mdeo5uY                下雨天            50       265846   
511996  1dKxf4Ht2SsKLyXfSDJAgy   The Cutest Puppy            67        82500   
511997  0SjsIzJkZfDU7wlcdklEFR  John Brown's Song            66       185250   
511998  5rgu12WBIHQtvej2MdHSH0                云与海            50       258267   
511999  0NuWgxEp51CutD2pJoF4OM              blind            72       153293   

        explicit             artists              id_artists release_date  \
0              0             ['Uli']  45tIt06XoI0Iio4LBEVpls   1922-02-22   
1              0             ['Uli']  45tIt06XoI0Iio4LBEVpls   1922-02-22   
2              0             ['Uli']  45tIt06XoI0Iio4LBEVpls   1922-02-22   
3              0             ['Uli']  45tIt06XoI0Iio4LBEVpls   1922-02-22   
4              0             ['Uli']  45tIt06XoI0Iio4LBEVpls   1922-02-22   
...          ...                 ...                     ...          ...   
511995         0              ['芝麻']  5VGgFE9nPgMfEnYiPT5J2B   2020-02-25   
511996         0  ['Laureen Conrad']  7vgGpuiXdNlCmc994PlMlz   2020-10-30   
511997         0  ['Gregory Oberle']  4MxqhahGRT4BPz1PilXGeu   2020-03-20   
511998         0         ['阿YueYue']  1QLBXKM5GCpyQQSVMNZqrZ   2020-09-26   
511999         0      ['ROLE MODEL']  1dy5WNgIKQU6ezkpZs4y8z   2020-10-21   

        danceability   energy  ...  time_signature    artists_upd_v1  \
0              0.645  0.44500  ...               3             [Uli]   
1              0.298  0.46000  ...               4             [Uli]   
2              0.634  0.00399  ...               4             [Uli]   
3              0.657  0.32500  ...               5             [Uli]   
4              0.644  0.68400  ...               4             [Uli]   
...              ...      ...  ...             ...               ...   
511995         0.528  0.67300  ...               4              [芝麻]   
511996         0.609  0.01720  ...               4  [Laureen Conrad]   
511997         0.562  0.03310  ...               3  [Gregory Oberle]   
511998         0.560  0.51800  ...               4         [阿YueYue]   
511999         0.765  0.66300  ...               4      [ROLE MODEL]   

        artists_upd_v2       artists_upd                     artists_song  \
0                   []             [Uli]                         UliCarve   
1                   []             [Uli]                      UliLazy Boi   
2                   []             [Uli]                        UliSketch   
3                   []             [Uli]                       UliL'enfer   
4                   []             [Uli]                      UliGraphite   
...                ...               ...                              ...   
511995              []              [芝麻]                            芝麻下雨天   
511996              []  [Laureen Conrad]   Laureen ConradThe Cutest Puppy   
511997              []  [Gregory Oberle]  Gregory OberleJohn Brown's Song   
511998              []         [阿YueYue]                       阿YueYue云与海   
511999              []      [ROLE MODEL]                  ROLE MODELblind   

        followers                                             genres  \
0            91.0                                                 []   
1            91.0                                                 []   
2            91.0                                                 []   
3            91.0                                               

In [ ]:
spotify_complete_df.dtypes

id                   object
name_x               object
popularity_x          int64
duration_ms           int64
explicit              int64
artists              object
id_artists           object
release_date         object
danceability        float64
energy              float64
key                   int64
loudness            float64
mode                  int64
speechiness         float64
acousticness        float64
instrumentalness    float64
liveness            float64
valence             float64
tempo               float64
time_signature        int64
artists_upd_v1       object
artists_upd_v2       object
artists_upd          object
artists_song         object
followers           float64
genres               object
name_y               object
popularity_y          int64
genres_upd           object
dtype: object

In [ ]:
spotify_complete_df['year'] = pd.DatetimeIndex(spotify_complete_df['release_date']).year

In [ ]:
spotify_complete_df = spotify_complete_df[["id", "name_x", "id_artists", "name_y", "popularity_x", "duration_ms", "explicit", "release_date", "year", "danceability", "energy", "key", "loudness", "mode", "speechiness", "acousticness", 
                                           "liveness", "valence", "tempo", "time_signature", "genres_upd", "followers", "popularity_y"]]

In [ ]:
spotify_complete_df.rename(columns = {'id':'song_id'}, inplace = True)
spotify_complete_df.rename(columns = {'name_x':'song_name'}, inplace = True)
spotify_complete_df.rename(columns = {'id_artists':'artist_id'}, inplace = True)
spotify_complete_df.rename(columns = {'name_y':'artist_name'}, inplace = True)
spotify_complete_df.rename(columns = {'popularity_x':'song_popularity'}, inplace = True)
spotify_complete_df.rename(columns = {'genres_upd':'genre'}, inplace = True)
spotify_complete_df.rename(columns = {'followers':'artist_followers'}, inplace = True)
spotify_complete_df.rename(columns = {'popularity_y':'artist_popularity'}, inplace = True)

In [ ]:
spotify_complete_df

song_id          song_name               artist_id  \
0       35iwgR4jXetI318WEWsa1Q              Carve  45tIt06XoI0Iio4LBEVpls   
1       0PH9AACae1f957JAavhOl2           Lazy Boi  45tIt06XoI0Iio4LBEVpls   
2       2SiNuAZ6jIU9xhClRKXcST             Sketch  45tIt06XoI0Iio4LBEVpls   
3       4vV7uBcF2AnjNTOejBS5oL            L'enfer  45tIt06XoI0Iio4LBEVpls   
4       598LlBn6jpEpVbLjmZPsYV           Graphite  45tIt06XoI0Iio4LBEVpls   
...                        ...                ...                     ...   
511995  0MmaEacabpK8Yp3Mdeo5uY                下雨天  5VGgFE9nPgMfEnYiPT5J2B   
511996  1dKxf4Ht2SsKLyXfSDJAgy   The Cutest Puppy  7vgGpuiXdNlCmc994PlMlz   
511997  0SjsIzJkZfDU7wlcdklEFR  John Brown's Song  4MxqhahGRT4BPz1PilXGeu   
511998  5rgu12WBIHQtvej2MdHSH0                云与海  1QLBXKM5GCpyQQSVMNZqrZ   
511999  0NuWgxEp51CutD2pJoF4OM              blind  1dy5WNgIKQU6ezkpZs4y8z   

           artist_name  song_popularity  duration_ms  explicit release_date  \
0                  Uli                6       126903         0   1922-02-22   
1                  Uli                0       157333         0   1922-02-22   
2                  Uli                0        87040         0   1922-02-22   
3                  Uli                0        40000         0   1922-02-22   
4                  Uli                0       104400         0   1922-02-22   
...                ...              ...          ...       ...          ...   
511995              芝麻               50       265846         0   2020-02-25   
511996  Laureen Conrad               67        82500         0   2020-10-30   
511997  Gregory Oberle               66       185250         0   2020-03-20   
511998         阿YueYue               50       258267         0   2020-09-26   
511999      ROLE MODEL               72       153293         0   2020-10-21   

        year  danceability  ...  mode  speechiness  acousticness  liveness  \
0       1922         0.645  ...     1       0.4510         0.674    0.1510   
1       1922         0.298  ...     1       0.4530         0.521    0.4360   
2       1922         0.634  ...     0       0.0377         0.926    0.1050   
3       1922         0.657  ...     0       0.2540         0.199    0.0931   
4       1922         0.644  ...     1       0.1990         0.144    0.0847   
...      ...           ...  ...   ...          ...           ...       ...   
511995  2020         0.528  ...     1       0.0314         0.143    0.0989   
511996  2020         0.609  ...     1       0.1180         0.996    0.1080   
511997  2020         0.562  ...     1       0.1030         0.996    0.1110   
511998  2020         0.560  ...     0       0.0292         0.785    0.0648   
511999  2020         0.765  ...     1       0.0652         0.141    0.0924   

        valence    tempo  time_signature  \
0         0.127  104.851               3   
1         0.402   87.921               4   
2         0.396   79.895               4   
3         0.105   81.944               5   
4         0.138  100.031               4   
...         ...      ...             ...   
511995    0.297  130.066               4   
511996    0.890   68.619               4   
511997    0.386   63.696               3   
511998    0.211  131.896               4   
511999    0.686  150.091               4   

                                                    genre  artist_followers  \
0                                                      []              91.0   
1                                                      []              91.0   
2                                                      []              91.0   
3                                                      []              91.0   
4                                                      []              91.0   
...                                                   ...               ...   
511995                                [chinese_viral_pop]             929.0   
511996                             [instrumental_lu

In [ ]:
spotify_complete_df.dtypes

song_id               object
song_name             object
artist_id             object
artist_name           object
song_popularity        int64
duration_ms            int64
explicit               int64
release_date          object
year                   int64
danceability         float64
energy               float64
key                    int64
loudness             float64
mode                   int64
speechiness          float64
acousticness         float64
liveness             float64
valence              float64
tempo                float64
time_signature         int64
genre                 object
artist_followers     float64
artist_popularity      int64
dtype: object

In [ ]:
spotify_complete_df.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\pre_processed_data.csv')

In [ ]:
spotify_complete_df[spotify_complete_df['artist_name'] == 'Martin Garrix'].head()

song_id                      song_name  \
285304  1TWfkGrhF7ob0nwB2M6knb                        Animals   
285305  5M9jOReAKGZ2AttVefFjTY  Don't Look Down (feat. Usher)   
285306  23L5CiUhw2jV1OIMwthR3S            In the Name of Love   
285307  3ebXMykcMXOcLeJ9xZ17XH            Scared to Be Lonely   
285308  6jA8HL9i4QGzsj6fjoxp8Y                  There for You   

                     artist_id    artist_name  song_popularity  duration_ms  \
285304  60d24wfXkVzDSfLS6hyCjZ  Martin Garrix               62       304229   
285305  60d24wfXkVzDSfLS6hyCjZ  Martin Garrix               66       223140   
285306  60d24wfXkVzDSfLS6hyCjZ  Martin Garrix               79       195707   
285307  60d24wfXkVzDSfLS6hyCjZ  Martin Garrix               80       220883   
285308  60d24wfXkVzDSfLS6hyCjZ  Martin Garrix               71       221904   

        explicit release_date  year  danceability  ...  mode  speechiness  \
285304         1   2013-07-01  2013         0.675  ...     1       0.0392   
285305         0   2015-03-17  2015         0.575  ...     1       0.0356   
285306         0   2016-07-29  2016         0.501  ...     0       0.0409   
285307         0   2017-01-27  2017         0.584  ...     0       0.0576   
285308         0   2017-05-26  2017         0.611  ...     0       0.0553   

        acousticness  liveness  valence    tempo  time_signature  \
285304       0.00107     0.374   0.0376  128.007               4   
285305       0.00406     0.111   0.3770  127.991               4   
285306       0.10900     0.454   0.1680  133.990               4   
285307       0.08950     0.261   0.1950  137.972               4   
285308       0.12400     0.124   0.1300  105.969               4   

                                                    genre  artist_followers  \
285304  [dance_pop, dutch_edm, edm, electro_house, pop...        14588353.0   
285305  [dance_pop, dutch_edm, edm, electro_house, pop...        14588353.0   
285306  [dance_pop, dutch_edm, edm, electro_house, pop...        14588353.0   
285307  [dance_pop, dutch_edm, edm, electro_house, pop...        14588353.0   
285308  [dance_pop, dutch_edm, edm, electro_house, pop...        14588353.0   

        artist_popularity  
285304                 83  
285305                 83  
285306                 83  
285307                 83  
285308                 83  

[5 rows x 23 columns]

#### Removing songs underepresented genres

In [ ]:
spotify_complete_df["genre"][10000]

['big_band', 'brass_ensemble']

In [ ]:
genres_count = {}

for song in tqdm(range(spotify_complete_df.shape[0])):
    for genre in spotify_complete_df["genre"][song]:
        if genre not in genres_count.keys():
            genres_count[genre] = 1
        else:
            genres_count[genre] += 1

100%|██████████████████████████████████████████████████████████████████████| 512000/512000 [00:04<00:00, 118593.27it/s]


In [ ]:
for genre in genres_count.keys():
    genres_count[genre] = genres_count[genre] / spotify_complete_df.shape[0]

In [ ]:
genres_count = dict(sorted(genres_count.items(), key=lambda item: item[1]))

In [ ]:
len(genres_count)

2200

In [ ]:
#genres_count

In [ ]:
genres_keep = {k:v for k,v in genres_count.items() if v > 1e-9}

In [ ]:
len(genres_keep)

2200

In [ ]:
#genres_filtered

In [ ]:
for song in tqdm(range(spotify_complete_df.shape[0])):
    for genre in spotify_complete_df["genre"][song]:
        if genre not in genres_keep.keys():
            spotify_complete_df["genre"][song].remove(genre)

100%|██████████████████████████████████████████████████████████████████████| 512000/512000 [00:04<00:00, 125295.75it/s]


In [ ]:
genres_count = {}

for song in tqdm(range(spotify_complete_df.shape[0])):
    for genre in spotify_complete_df["genre"][song]:
        if genre not in genres_count.keys():
            genres_count[genre] = 1
        else:
            genres_count[genre] += 1

100%|██████████████████████████████████████████████████████████████████████| 512000/512000 [00:04<00:00, 121403.81it/s]


In [ ]:
genres_count = dict(sorted(genres_count.items(), key=lambda item: item[1]))

In [ ]:
len(genres_count)

2200

In [ ]:
genres_count

{'pre-war_blues': 1,
 'british_black_metal': 1,
 'uk_doom_metal': 1,
 'vintage_gospel': 1,
 'historic_string_quartet': 1,
 'czech_classical_piano': 1,
 'historic_piano_performance': 1,
 'vintage_spanish_pop': 1,
 'ukrainian_electronic': 1,
 'oratory': 1,
 'classic_azeri_pop': 1,
 'afghan_traditional': 1,
 'electroacoustic_composition': 1,
 'rare_groove': 1,
 'khmer': 1,
 'atmospheric_dnb': 1,
 'korean_classical_piano': 1,
 'stockholm_indie': 1,
 'klezmer': 1,
 'italian_modern_prog': 1,
 'kent_indie': 1,
 'italo_dance': 1,
 'progressive_doom': 1,
 'brazilian_power_metal': 1,
 'progressive_sludge': 1,
 'stoner_metal': 1,
 'depressive_black_metal': 1,
 'italian_doom_metal': 1,
 'mathgrind': 1,
 'paisley_underground': 1,
 'comedy': 1,
 'neofolk': 1,
 'cologne_electronic': 1,
 'dutch_prog': 1,
 'oakland_indie': 1,
 'scottish_indie_folk': 1,
 'dutch_tech_house': 1,
 'metallic_hardcore': 1,
 'senegalese_traditional': 1,
 'griot': 1,
 'concert_band': 1,
 'bubblegrunge': 1,
 'uptempo_hardcore':

## Feature Engineering

In [ ]:
spotify_complete_df.head()

song_id song_name               artist_id artist_name  \
0  35iwgR4jXetI318WEWsa1Q     Carve  45tIt06XoI0Iio4LBEVpls         Uli   
1  0PH9AACae1f957JAavhOl2  Lazy Boi  45tIt06XoI0Iio4LBEVpls         Uli   
2  2SiNuAZ6jIU9xhClRKXcST    Sketch  45tIt06XoI0Iio4LBEVpls         Uli   
3  4vV7uBcF2AnjNTOejBS5oL   L'enfer  45tIt06XoI0Iio4LBEVpls         Uli   
4  598LlBn6jpEpVbLjmZPsYV  Graphite  45tIt06XoI0Iio4LBEVpls         Uli   

   song_popularity  duration_ms  explicit release_date  year  danceability  \
0                6       126903         0   1922-02-22  1922         0.645   
1                0       157333         0   1922-02-22  1922         0.298   
2                0        87040         0   1922-02-22  1922         0.634   
3                0        40000         0   1922-02-22  1922         0.657   
4                0       104400         0   1922-02-22  1922         0.644   

   ...  mode  speechiness  acousticness  liveness  valence    tempo  \
0  ...     1       0.4510         0.674    0.1510    0.127  104.851   
1  ...     1       0.4530         0.521    0.4360    0.402   87.921   
2  ...     0       0.0377         0.926    0.1050    0.396   79.895   
3  ...     0       0.2540         0.199    0.0931    0.105   81.944   
4  ...     1       0.1990         0.144    0.0847    0.138  100.031   

   time_signature  genre  artist_followers  artist_popularity  
0               3     []              91.0                  4  
1               4     []              91.0                  4  
2               4     []              91.0                  4  
3               5     []              91.0                  4  
4               4     []              91.0                  4  

[5 rows x 23 columns]

In [ ]:
spotify_complete_df.dtypes

song_id               object
song_name             object
artist_id             object
artist_name           object
song_popularity        int64
duration_ms            int64
explicit               int64
release_date          object
year                   int64
danceability         float64
energy               float64
key                    int64
loudness             float64
mode                   int64
speechiness          float64
acousticness         float64
liveness             float64
valence              float64
tempo                float64
time_signature         int64
genre                 object
artist_followers     float64
artist_popularity      int64
dtype: object

In [ ]:
spotify_complete_df['song_popularity'] = spotify_complete_df['song_popularity'].apply(lambda x: int(x/5))

In [ ]:
# Function to create OHE features
def ohe_prep(df, column, new_name): 
    
    tf_df = pd.get_dummies(df[column])
    feature_names = tf_df.columns
    tf_df.columns = [new_name + "|" + str(i) for i in feature_names]
    tf_df.reset_index(drop = True, inplace = True) 
    
    return tf_df

In [ ]:
# Function to build entire feature set
def create_feature_set(df, extra_cols):
    
    #tfidf genre lists
    tfidf = TfidfVectorizer()
    tfidf_matrix =  tfidf.fit_transform(spotify_complete_df['genre'].apply(lambda x: " ".join(x)))
    genre_df = pd.DataFrame(tfidf_matrix.toarray())
    genre_df.columns = ['genre' + "|" + i for i in tfidf.get_feature_names()]
    genre_df.reset_index(drop = True, inplace=True)
  
    year_ohe = ohe_prep(df, 'year','year') * 0.3
    popularity_ohe = ohe_prep(df, 'song_popularity','song_popularity') * 0.15

    #scale float columns
    extras = df[extra_cols].reset_index(drop = True)
    scaler = MinMaxScaler()
    extra_scaled = pd.DataFrame(scaler.fit_transform(extras), columns = extras.columns) * 0.2
    
    #concanenate all features
    final = pd.concat([extra_scaled, genre_df, year_ohe, popularity_ohe], axis = 1)
    
    # add song id
    final['song_id']=df['song_id'].values
    
    return final

In [ ]:
extra_cols = ["danceability", "energy", "loudness", "speechiness", "acousticness", "liveness", "valence", "tempo"]

In [ ]:
complete_feature_set = create_feature_set(spotify_complete_df, extra_cols=extra_cols)

In [ ]:
pd.set_option('display.max_columns', 10000)

In [ ]:
complete_feature_set.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\complete_feature_set.csv')

In [ ]:
complete_feature_set

danceability    energy  loudness  speechiness  acousticness  liveness  \
0           0.130172  0.089000  0.142750     0.092894      0.135341   0.03020   
1           0.060141  0.092000  0.126514     0.093306      0.104618   0.08720   
2           0.127952  0.000798  0.091859     0.007765      0.185944   0.02100   
3           0.132593  0.065000  0.139749     0.052317      0.039960   0.01862   
4           0.129970  0.136800  0.158324     0.040989      0.028916   0.01694   
...              ...       ...       ...          ...           ...       ...   
511995      0.106559  0.134600  0.172421     0.006468      0.028715   0.01978   
511996      0.122906  0.003440  0.096142     0.024305      0.200000   0.02160   
511997      0.113421  0.006620  0.105387     0.021215      0.200000   0.02220   
511998      0.113017  0.103600  0.160698     0.006014      0.157631   0.01296   
511999      0.154390  0.132600  0.167575     0.013429      0.028313   0.01848   

        valence     tempo  genre|21st_century_classical  genre|432hz  \
0        0.0254  0.085113                           0.0          0.0   
1        0.0804  0.071370                           0.0          0.0   
2        0.0792  0.064855                           0.0          0.0   
3        0.0210  0.066518                           0.0          0.0   
4        0.0276  0.081200                           0.0          0.0   
...         ...       ...                           ...          ...   
511995   0.0594  0.105581                           0.0          0.0   
511996   0.1780  0.055702                           0.0          0.0   
511997   0.0772  0.051705                           0.0          0.0   
511998   0.0422  0.107067                           0.0          0.0   
511999   0.1372  0.121837                           0.0          0.0   

        genre|48g  genre|_brasileira  genre|_hip_hop  genre|_house  \
0             0.0                0.0             0.0           0.0   
1             0.0                0.0             0.0           0.0   
2             0.0                0.0             0.0           0.0   
3             0.0                0.0             0.0           0.0   
4             0.0                0.0             0.0           0.0   
...           ...                ...             ...           ...   
511995        0.0                0.0             0.0           0.0   
511996        0.0                0.0             0.0           0.0   
511997        0.0                0.0             0.0           0.0   
511998        0.0                0.0             0.0           0.0   
511999        0.0                0.0             0.0           0.0   

        genre|a_cappella  genre|abstract  genre|abstract_beats  \
0                    0.0             0.0                   0.0   
1                    0.0             0.0                   0.0   
2                    0.0             0.0                   0.0   
3                    0.0             0.0                   0.0   
4                    0.0             0.0                   0.0   
...                  ...             ...                   ...   
511995               0.0             0.0                   0.0   
511996               0.0             0.0                   0.0   
511997               0.0             0.0                   0.0   
511998               0.0             0.0                   0.0   
511999               0.0             0.0                   0.0   

        genre|abstract_hip_hop  genre|abstract_idm  genre|accordeon  \
0                          0.0                 0.0              0.0   
1                          0.0                 0.0              0.0   
2                          0.0                 0.0              0.0   
3                          0.0                 0.0              0.0   
4                          0.0                 0.0              0.0   
...                        ...                 ...              ...   
511995                     0.0         

## Connecting to Spotify

In [ ]:
#client id and secret for my application
client_id = 'acf0813d383e41ce91512bXXXXXXXXXX'
client_secret= '21074895d8ac47da8f7bfeXXXXXXXXXX'

In [ ]:
scope = 'user-library-read'

if len(sys.argv) > 1:
    username = sys.argv[1]
else:
    print("Usage: %s username" % (sys.argv[0],))
    sys.exit()

In [ ]:
auth_manager = SpotifyClientCredentials(client_id=client_id, client_secret=client_secret)
sp = spotipy.Spotify(auth_manager=auth_manager)

In [ ]:
token = util.prompt_for_user_token(scope, client_id= client_id, client_secret=client_secret, redirect_uri='http://localhost:4242/')

In [ ]:
sp = spotipy.Spotify(auth=token)

In [ ]:
# Get user playlists
id_name = {}
for i in sp.current_user_playlists()['items']:
    id_name[i['name']] = i['uri'].split(':')[2]

In [ ]:
id_name

{'Classical': '17rdNT3FjFxcLZla276jkZ',
 'Rap': '24xfNCEXdDUgoEce2FwDMa',
 '80s Rock Anthems': '37i9dQZF1DX1spT6G94GFC',
 'EDM Classics (Top 100)': '1lS6v9h4MXOw6f6y8MkS8w',
 'Music_inf': '19d2gPGPJs3asC8vY3tOXv',
 'Rock_music': '4SYofQUj7wYoJdsSMnrCHA',
 'EDM_MUSIC_TEST': '4rYzi8jAv43v6PDICSDqCW',
 'ROPE': '4TbbGmk09hLAXZYPv0u72I',
 'SummeRoPe 🧞\u200d♂️☀️😎': '6Pd2tq2nTNut2tMg7SmGT7',
 'Bless Boost by San Holo': '4SyzXM642LPo1bI7rThGyO',
 'Summer': '3KWX6XO4A8rsjXB4qIMjLd',
 'ThisPlaylistIsGreat': '2Ig4JRDcBuKjpUp02Nisfo',
 'ThisPlaylistIsGood': '6MWAp1QP6IvCQRC1QDBnki',
 'MyChillnLofi': '0zqmFZNB0zksUTgN89jRJU',
 'FL studio insp': '5fkcHkldhfH6ZdDE10ZBXO',
 'ElectronIndie': '7KLireqZ0EvtQniZoZnu0o',
 'Playlist': '6fmuWFCEY9c1XPpxpyZCmi',
 'Tomorrowland': '1MD0i7RFlPOWZUtXExyWIO',
 'CHILL1': '4eqyI5x5p5qgiwtYMBDGuj',
 'Rn_b': '6QRwIG4nAv5etOlRkZKnGA',
 'Don Diablo': '0I3Um6hdF3nvCK1BenGDCm',
 'Good vibes // EDM R&B Chill': '06bw8lQZglkrqOvmHhoUar',
 'My Shazam Tracks': '0qjLoHGLGF0889N

## Creating Playlist Vector

In [ ]:
def create_necessary_outputs(playlist_name,id_dic, df):
    
    #generate playlist dataframe
    playlist = pd.DataFrame()
    playlist_name = playlist_name

    for ix, i in enumerate(sp.playlist(id_dic[playlist_name])['tracks']['items']):
        #print(i['track']['artists'][0]['name'])
        playlist.loc[ix, 'artist'] = i['track']['artists'][0]['name']
        playlist.loc[ix, 'name'] = i['track']['name']
        playlist.loc[ix, 'song_id'] = i['track']['id'] # ['uri'].split(':')[2]
        playlist.loc[ix, 'url'] = i['track']['album']['images'][1]['url']
        playlist.loc[ix, 'date_added'] = i['added_at']

    playlist['date_added'] = pd.to_datetime(playlist['date_added'])  
    
    playlist = playlist[playlist['song_id'].isin(df['song_id'].values)].sort_values('date_added',ascending = False)
    
    return playlist

In [ ]:
spotify_complete_df = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\pre_processed_data.csv')

In [ ]:
playlist_ROPE = create_necessary_outputs('Classical', id_name, spotify_complete_df)

In [ ]:
playlist_ROPE

artist  \
0                        Johann Sebastian Bach   
78                       Johann Nepomuk Hummel   
50                     Samuel Coleridge-Taylor   
53  Joseph Boulogne Chevalier de Saint-Georges   
57                             George Gershwin   
59                               Gabriel Fauré   
60                    Pyotr Ilyich Tchaikovsky   
64                       Johann Sebastian Bach   
66                         Dmitri Shostakovich   
74                                André Previn   
75                               Jean Sibelius   
77                     Wolfgang Amadeus Mozart   
80                              Antonín Dvořák   
2                         Ludwig van Beethoven   
81                            Frederick Delius   
83                             Frédéric Chopin   
85                     Wolfgang Amadeus Mozart   
86                           Ottorino Respighi   
87                    Pyotr Ilyich Tchaikovsky   
92                               Aaron Copland   
94                        Ludwig van Beethoven   
96                               Georges Bizet   
97                              Franz Schubert   
98                    Pyotr Ilyich Tchaikovsky   
48                               Gabriel Fauré   
47                            Niccolò Paganini   
46                                Edvard Grieg   
45                             Giacomo Puccini   
4                             Johann Pachelbel   
5                       George Frideric Handel   
7                          Camille Saint-Saëns   
10                           Johann Strauss II   
12                               Gustav Mahler   
16                        Ludwig van Beethoven   
17                     Nikolai Rimsky-Korsakov   
18                                Edward Elgar   
20                                 Franz Liszt   
21                                 Franz Liszt   
22                               Jean Sibelius   
25                                 Max Richter   
26                            Sergei Prokofiev   
27                         Sergei Rachmaninoff   
29                               Samuel Barber   
30                           Aram Khachaturian   
37                                   Arvo Pärt   
38                              Franz Schubert   
39                                  Paul Dukas   
40                             Johannes Brahms   
43                             Frédéric Chopin   
99                                Jan Garbarek   

                                                                                                    name  \
0                                                     Cello Suite No. 1 in G Major, BWV 1007: I. Prélude   
78                                                        Hummel: Trumpet Concerto In E Flat - Iii Rondo   
50                                                        Symphonic Variations on an African Air, Op. 63   
53                                                              Violin Concerto No. 10 in G Major: Largo   
57                                                                                      Rhapsody In Blue   
59                                                           Pelléas et Mélisande, Op. 80: 4. Sicilienne   
60                         Serenade for Strings in C major, Op. 48: II. Walzer: Moderato, tempo di valse   
64                                               St. Matthew Passion, BWV 244 / Part Two: "Erbarme dich"   
66                                                            Cello Concerto No.1, Op.107: 1. Allegretto   
74                                                          Tsar Saltan, Op. 57: Flight of the Bumblebee   
75                                              Symphony No. 5 in E-Flat Major, Op. 82: 3. Allegro molto   
77                                   Sonata for 2 Pianos in D Major, K. 448/375a: I. Allegro con spirito   
80                                    Serenade for Strings in E Major, Op. 22, B. 52:

In [ ]:
def generate_playlist_feature(complete_feature_set, playlist_df):
    
    complete_feature_set_playlist = complete_feature_set[complete_feature_set['song_id'].isin(playlist_df['song_id'].values)]
    complete_feature_set_playlist = complete_feature_set_playlist.merge(playlist_df[['song_id','date_added']], on = 'song_id', how = 'inner')
    complete_feature_set_nonplaylist = complete_feature_set[~complete_feature_set['song_id'].isin(playlist_df['song_id'].values)]
    
    return complete_feature_set_playlist.sum(axis = 0), complete_feature_set_playlist, complete_feature_set_nonplaylist

In [ ]:
complete_feature_set = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\complete_feature_set.csv')

In [ ]:
playlist_vector, playlist_song_vector, non_playlist_song_vector = generate_playlist_feature(complete_feature_set=complete_feature_set, playlist_df=playlist_ROPE)

In [ ]:
playlist_vector

Unnamed: 0                                                      3107851
danceability                                                   2.423835
energy                                                         0.876404
loudness                                                       5.480317
speechiness                                                    0.445273
                                            ...                        
song_popularity|17                                                  0.0
song_popularity|18                                                  0.0
song_popularity|19                                                  0.0
song_popularity|20                                                  0.0
song_id               17i5jLpzndlQhbS4SrTd0B58Q96yWnuBqlKEGd2vGyAg0y...
Length: 4621, dtype: object

In [ ]:
playlist_song_vector

Unnamed: 0  danceability    energy  loudness  speechiness  acousticness  \
0         4445      0.055499  0.031400  0.126187     0.013100      0.178715   
1         4466      0.048436  0.012960  0.106437     0.008774      0.187751   
2         9969      0.062361  0.051600  0.136665     0.009454      0.195984   
3        13397      0.037134  0.001054  0.069555     0.008898      0.199799   
4        13915      0.018769  0.004980  0.120105     0.009537      0.103012   
5        13925      0.058325  0.006120  0.089360     0.009186      0.198193   
6        14601      0.020161  0.004820  0.105081     0.008898      0.196787   
7        14707      0.076085  0.034600  0.118157     0.006756      0.198996   
8        17406      0.082947  0.009740  0.104993     0.007889      0.197791   
9        17412      0.045409  0.000940  0.088938     0.010484      0.199197   
10       18425      0.020585  0.014660  0.109725     0.010051      0.195582   
11       19063      0.041372  0.010500  0.110619     0.006735      0.196787   
12       19140      0.042180  0.020200  0.124257     0.008301      0.186145   
13       19617      0.060343  0.001252  0.088953     0.009846      0.199598   
14       19933      0.042785  0.060200  0.145298     0.007909      0.193373   
15       20637      0.073461  0.011840  0.116994     0.011740      0.196386   
16       20764      0.034914  0.036400  0.125893     0.009001      0.177912   
17       20780      0.031483  0.001418  0.079072     0.007868      0.188956   
18       20955      0.048638  0.024400  0.114993     0.010237      0.185743   
19       21171      0.056307  0.005840  0.101554     0.008363      0.198193   
20       21217      0.068819  0.002840  0.096999     0.007992      0.199398   
21       21653      0.033098  0.003880  0.079154     0.008939      0.188353   
22       21679      0.074672  0.001520  0.080571     0.007909      0.199799   
23       21981      0.047023  0.005040  0.107611     0.007127      0.195783   
24       22504      0.000000  0.016840  0.124214     0.000000      0.151606   
25       22720      0.034107  0.003220  0.088614     0.009104      0.197992   
26       22849      0.087992  0.030200  0.120090     0.012420      0.191767   
27       29566      0.030474  0.012780  0.108896     0.009042      0.193173   
28       32473      0.069223  0.004180  0.100909     0.008198      0.198193   
29       32476      0.020182  0.007080  0.130901     0.007971      0.180924   
30       39034      0.032694  0.027800  0.120246     0.007951      0.173695   
31       39068      0.022805  0.032200  0.122228     0.009104      0.097189   
32       40409      0.070838  0.041200  0.114241     0.012297      0.160040   
33       41153      0.029869  0.014440  0.106409     0.008795      0.189558   
34       41268      0.015802  0.010460  0.112436     0.009701      0.179920   
35       42355      0.093845  0.025600  0.129626     0.010690      0.196386   
36       48388      0.093441  0.032400  0.108651     0.009269      0.193373   
37       48622      0.037538  0.024800  0.136836     0.008939      0.196386   
38       48683      0.033300  0.021200  0.117040     0.008033      0.162048   
39       48927      0.015217  0.002040  0.074370     0.009557      0.180924   
40       52601      0.018951  0.006720  0.110007     0.012482      0.186145   
41       59387      0.014450  0.008160  0.097026     0.008218      0.170884   
42       66403      0.092432  0.022000  0.115535     0.006365      0.196185   
43       86278      0.025832  0.026400  0.129497     0.007271      0.149398   
44      189289      0.035520  0.001200  0.054338     0.007909      0.180522   
45      228082      0.045207  0.005820  0.103503     0.009372      0.192570   
46      230555      0.038951  0.013120  0.124697     0.009701      0.199799   
47      286250      0.141473  0.068200  0.146047     0.008610      0.100201   
48      429155      0.042785  0.010340  0.108703     0.010814      0.186345   
49      468098      0.100101  0.049800  0.128087     0

In [ ]:
non_playlist_song_vector

Unnamed: 0  danceability    energy  loudness  speechiness  \
0                0      0.130172  0.089000  0.142750     0.092894   
1                1      0.060141  0.092000  0.126514     0.093306   
2                2      0.127952  0.000798  0.091859     0.007765   
3                3      0.132593  0.065000  0.139749     0.052317   
4                4      0.129970  0.136800  0.158324     0.040989   
...            ...           ...       ...       ...          ...   
511995      511995      0.106559  0.134600  0.172421     0.006468   
511996      511996      0.122906  0.003440  0.096142     0.024305   
511997      511997      0.113421  0.006620  0.105387     0.021215   
511998      511998      0.113017  0.103600  0.160698     0.006014   
511999      511999      0.154390  0.132600  0.167575     0.013429   

        acousticness  liveness  valence     tempo  \
0           0.135341   0.03020   0.0254  0.085113   
1           0.104618   0.08720   0.0804  0.071370   
2           0.185944   0.02100   0.0792  0.064855   
3           0.039960   0.01862   0.0210  0.066518   
4           0.028916   0.01694   0.0276  0.081200   
...              ...       ...      ...       ...   
511995      0.028715   0.01978   0.0594  0.105581   
511996      0.200000   0.02160   0.1780  0.055702   
511997      0.200000   0.02220   0.0772  0.051705   
511998      0.157631   0.01296   0.0422  0.107067   
511999      0.028313   0.01848   0.1372  0.121837   

        genre|21st_century_classical  ...  song_popularity|12  \
0                                0.0  ...                 0.0   
1                                0.0  ...                 0.0   
2                                0.0  ...                 0.0   
3                                0.0  ...                 0.0   
4                                0.0  ...                 0.0   
...                              ...  ...                 ...   
511995                           0.0  ...                 0.0   
511996                           0.0  ...                 0.0   
511997                           0.0  ...                 0.0   
511998                           0.0  ...                 0.0   
511999                           0.0  ...                 0.0   

        song_popularity|13  song_popularity|14  song_popularity|15  \
0                     0.00                0.00                 0.0   
1                     0.00                0.00                 0.0   
2                     0.00                0.00                 0.0   
3                     0.00                0.00                 0.0   
4                     0.00                0.00                 0.0   
...                    ...                 ...                 ...   
511995                0.00                0.00                 0.0   
511996                0.15                0.00                 0.0   
511997                0.15                0.00                 0.0   
511998                0.00                0.00                 0.0   
511999                0.00                0.15                 0.0   

        song_popularity|16  song_popularity|17  song_popularity|18  \
0                      0.0                 0.0                 0.0   
1                      0.0                 0.0                 0.0   
2                      0.0                 0.0                 0.0   
3                      0.0                 0.0                 0.0   
4                      0.0                 0.0                 0.0   
...                    ...                 ...                 ...   
511995                 0.0                 0.0                 0.0   
511996                 0.0                 0.0                 0.0   
511997                 0.0                 0.0                 0.0   
511998                 0.0                 0.0                 0.0   
511999                 0.0                 0.0                 0.0   

        song_popularity|19  song_popularity|20                 song_id  
0     

In [ ]:
playlist_vector.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\playlist_vector.csv')

In [ ]:
playlist_song_vector.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\playlist_song_vector.csv')

In [ ]:
non_playlist_song_vector.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\non_playlist_song_vector.csv')

## Generate Recommendations

In [ ]:
spotify_complete_df = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\\P5\\DT2470 Music Informatics\\Project\\_Data\\pre_processed_data.csv')

In [ ]:
playlist_vector = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\playlist_vector.csv')

In [ ]:
playlist_song_vector = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_EDM_2020s\\playlist_song_vector.csv')

In [ ]:
non_playlist_song_vector = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\non_playlist_song_vector.csv')

In [ ]:
spotify_complete_df = spotify_complete_df.drop(columns=["Unnamed: 0"])
playlist_vector = playlist_vector.drop(columns=["Unnamed: 0"])
playlist_song_vector = playlist_song_vector.drop(columns=["Unnamed: 0"])
playlist_song_vector = playlist_song_vector.drop(columns=["Unnamed: 0.1"])
non_playlist_song_vector = non_playlist_song_vector.drop(columns=["Unnamed: 0"])
non_playlist_song_vector = non_playlist_song_vector.drop(columns=["Unnamed: 0.1"])

In [ ]:
playlist_vector = playlist_vector.drop(columns=["Unnamed: 0"])
playlist_song_vector = playlist_song_vector.drop(columns=["Unnamed: 0"])
playlist_song_vector = playlist_song_vector.drop(columns=["Unnamed: 0.1"])

In [ ]:
# Remove "unnamed" feature and song_id, won't be need for cosine similarity as it only looks at floats (forming vectors) where strings are unusable
playlist_vector = playlist_vector.iloc[1: , :]
playlist_vector = playlist_vector[:-1]

In [ ]:
spotify_complete_df

song_id          song_name               artist_id  \
0       35iwgR4jXetI318WEWsa1Q              Carve  45tIt06XoI0Iio4LBEVpls   
1       0PH9AACae1f957JAavhOl2           Lazy Boi  45tIt06XoI0Iio4LBEVpls   
2       2SiNuAZ6jIU9xhClRKXcST             Sketch  45tIt06XoI0Iio4LBEVpls   
3       4vV7uBcF2AnjNTOejBS5oL            L'enfer  45tIt06XoI0Iio4LBEVpls   
4       598LlBn6jpEpVbLjmZPsYV           Graphite  45tIt06XoI0Iio4LBEVpls   
...                        ...                ...                     ...   
511995  0MmaEacabpK8Yp3Mdeo5uY                下雨天  5VGgFE9nPgMfEnYiPT5J2B   
511996  1dKxf4Ht2SsKLyXfSDJAgy   The Cutest Puppy  7vgGpuiXdNlCmc994PlMlz   
511997  0SjsIzJkZfDU7wlcdklEFR  John Brown's Song  4MxqhahGRT4BPz1PilXGeu   
511998  5rgu12WBIHQtvej2MdHSH0                云与海  1QLBXKM5GCpyQQSVMNZqrZ   
511999  0NuWgxEp51CutD2pJoF4OM              blind  1dy5WNgIKQU6ezkpZs4y8z   

           artist_name  song_popularity  duration_ms  explicit release_date  \
0                  Uli                6       126903         0   1922-02-22   
1                  Uli                0       157333         0   1922-02-22   
2                  Uli                0        87040         0   1922-02-22   
3                  Uli                0        40000         0   1922-02-22   
4                  Uli                0       104400         0   1922-02-22   
...                ...              ...          ...       ...          ...   
511995              芝麻               50       265846         0   2020-02-25   
511996  Laureen Conrad               67        82500         0   2020-10-30   
511997  Gregory Oberle               66       185250         0   2020-03-20   
511998         阿YueYue               50       258267         0   2020-09-26   
511999      ROLE MODEL               72       153293         0   2020-10-21   

        year  danceability  ...  mode  speechiness  acousticness  liveness  \
0       1922         0.645  ...     1       0.4510         0.674    0.1510   
1       1922         0.298  ...     1       0.4530         0.521    0.4360   
2       1922         0.634  ...     0       0.0377         0.926    0.1050   
3       1922         0.657  ...     0       0.2540         0.199    0.0931   
4       1922         0.644  ...     1       0.1990         0.144    0.0847   
...      ...           ...  ...   ...          ...           ...       ...   
511995  2020         0.528  ...     1       0.0314         0.143    0.0989   
511996  2020         0.609  ...     1       0.1180         0.996    0.1080   
511997  2020         0.562  ...     1       0.1030         0.996    0.1110   
511998  2020         0.560  ...     0       0.0292         0.785    0.0648   
511999  2020         0.765  ...     1       0.0652         0.141    0.0924   

        valence    tempo  time_signature  \
0         0.127  104.851               3   
1         0.402   87.921               4   
2         0.396   79.895               4   
3         0.105   81.944               5   
4         0.138  100.031               4   
...         ...      ...             ...   
511995    0.297  130.066               4   
511996    0.890   68.619               4   
511997    0.386   63.696               3   
511998    0.211  131.896               4   
511999    0.686  150.091               4   

                                                    genre  artist_followers  \
0                                                      []              91.0   
1                                                      []              91.0   
2                                                      []              91.0   
3                                                      []              91.0   
4                                                      []              91.0   
...                                                   ...               ...   
511995                              ['chinese_viral_pop']             929.0   
511996                           ['instrumental_lul

In [ ]:
playlist_vector

0
1      7.254086781029262
2                10.6196
3     10.699495227606459
4     0.7380226570545793
5     1.3091346706827278
...                  ...
4615                1.35
4616                 0.3
4617                 0.0
4618                 0.0
4619                 0.0

[4619 rows x 1 columns]

In [ ]:
playlist_song_vector

danceability    energy  loudness  speechiness  acousticness  liveness  \
0       0.055499  0.031400  0.126187     0.013100      0.178715   0.03720   
1       0.048436  0.012960  0.106437     0.008774      0.187751   0.05160   
2       0.062361  0.051600  0.136665     0.009454      0.195984   0.01848   
3       0.037134  0.001054  0.069555     0.008898      0.199799   0.03460   
4       0.018769  0.004980  0.120105     0.009537      0.103012   0.01662   
5       0.058325  0.006120  0.089360     0.009186      0.198193   0.02040   
6       0.020161  0.004820  0.105081     0.008898      0.196787   0.01246   
7       0.076085  0.034600  0.118157     0.006756      0.198996   0.02100   
8       0.082947  0.009740  0.104993     0.007889      0.197791   0.01888   
9       0.045409  0.000940  0.088938     0.010484      0.199197   0.01444   
10      0.020585  0.014660  0.109725     0.010051      0.195582   0.05600   
11      0.041372  0.010500  0.110619     0.006735      0.196787   0.02060   
12      0.042180  0.020200  0.124257     0.008301      0.186145   0.01552   
13      0.060343  0.001252  0.088953     0.009846      0.199598   0.01646   
14      0.042785  0.060200  0.145298     0.007909      0.193373   0.02600   
15      0.073461  0.011840  0.116994     0.011740      0.196386   0.01646   
16      0.034914  0.036400  0.125893     0.009001      0.177912   0.04480   
17      0.031483  0.001418  0.079072     0.007868      0.188956   0.01972   
18      0.048638  0.024400  0.114993     0.010237      0.185743   0.02520   
19      0.056307  0.005840  0.101554     0.008363      0.198193   0.02080   
20      0.068819  0.002840  0.096999     0.007992      0.199398   0.02260   
21      0.033098  0.003880  0.079154     0.008939      0.188353   0.01878   
22      0.074672  0.001520  0.080571     0.007909      0.199799   0.01728   
23      0.047023  0.005040  0.107611     0.007127      0.195783   0.02860   
24      0.000000  0.016840  0.124214     0.000000      0.151606   0.05240   
25      0.034107  0.003220  0.088614     0.009104      0.197992   0.01610   
26      0.087992  0.030200  0.120090     0.012420      0.191767   0.02200   
27      0.030474  0.012780  0.108896     0.009042      0.193173   0.09320   
28      0.069223  0.004180  0.100909     0.008198      0.198193   0.02520   
29      0.020182  0.007080  0.130901     0.007971      0.180924   0.02500   
30      0.032694  0.027800  0.120246     0.007951      0.173695   0.04320   
31      0.022805  0.032200  0.122228     0.009104      0.097189   0.03200   
32      0.070838  0.041200  0.114241     0.012297      0.160040   0.01476   
33      0.029869  0.014440  0.106409     0.008795      0.189558   0.02300   
34      0.015802  0.010460  0.112436     0.009701      0.179920   0.01612   
35      0.093845  0.025600  0.129626     0.010690      0.196386   0.00846   
36      0.093441  0.032400  0.108651     0.009269      0.193373   0.01886   
37      0.037538  0.024800  0.136836     0.008939      0.196386   0.02220   
38      0.033300  0.021200  0.117040     0.008033      0.162048   0.02100   
39      0.015217  0.002040  0.074370     0.009557      0.180924   0.01634   
40      0.018951  0.006720  0.110007     0.012482      0.186145   0.01908   
41      0.014450  0.008160  0.097026     0.008218      0.170884   0.01688   
42      0.092432  0.022000  0.115535     0.006365      0.196185   0.07180   
43      0.025832  0.026400  0.129497     0.007271      0.149398   0.02140   
44      0.035520  0.001200  0.054338     0.007909      0.180522   0.02100   
45      0.045207  0.005820  0.103503     0.009372      0.192570   0.02200   
46      0.038951  0.013120  0.124697     0.009701      0.199799   0.02380   
47      0.141473  0.068200  0.146047     0.008610      0.100201   0.07180   
48      0.042785  0.010340  0.108703     0.010814      0.186345   0.02240   
49      0.100101  0.049800  0.128087     0.008465      0.196787   0.02400   

    valence     tempo  genre|21st_century_classical  genre|432hz  ...  \
0  

In [ ]:
non_playlist_song_vector

danceability    energy  loudness  speechiness  acousticness  liveness  \
0           0.130172  0.089000  0.142750     0.092894      0.135341   0.03020   
1           0.060141  0.092000  0.126514     0.093306      0.104618   0.08720   
2           0.127952  0.000798  0.091859     0.007765      0.185944   0.02100   
3           0.132593  0.065000  0.139749     0.052317      0.039960   0.01862   
4           0.129970  0.136800  0.158324     0.040989      0.028916   0.01694   
...              ...       ...       ...          ...           ...       ...   
511945      0.106559  0.134600  0.172421     0.006468      0.028715   0.01978   
511946      0.122906  0.003440  0.096142     0.024305      0.200000   0.02160   
511947      0.113421  0.006620  0.105387     0.021215      0.200000   0.02220   
511948      0.113017  0.103600  0.160698     0.006014      0.157631   0.01296   
511949      0.154390  0.132600  0.167575     0.013429      0.028313   0.01848   

        valence     tempo  genre|21st_century_classical  genre|432hz  ...  \
0        0.0254  0.085113                           0.0          0.0  ...   
1        0.0804  0.071370                           0.0          0.0  ...   
2        0.0792  0.064855                           0.0          0.0  ...   
3        0.0210  0.066518                           0.0          0.0  ...   
4        0.0276  0.081200                           0.0          0.0  ...   
...         ...       ...                           ...          ...  ...   
511945   0.0594  0.105581                           0.0          0.0  ...   
511946   0.1780  0.055702                           0.0          0.0  ...   
511947   0.0772  0.051705                           0.0          0.0  ...   
511948   0.0422  0.107067                           0.0          0.0  ...   
511949   0.1372  0.121837                           0.0          0.0  ...   

        song_popularity|12  song_popularity|13  song_popularity|14  \
0                      0.0                0.00                0.00   
1                      0.0                0.00                0.00   
2                      0.0                0.00                0.00   
3                      0.0                0.00                0.00   
4                      0.0                0.00                0.00   
...                    ...                 ...                 ...   
511945                 0.0                0.00                0.00   
511946                 0.0                0.15                0.00   
511947                 0.0                0.15                0.00   
511948                 0.0                0.00                0.00   
511949                 0.0                0.00                0.15   

        song_popularity|15  song_popularity|16  song_popularity|17  \
0                      0.0                 0.0                 0.0   
1                      0.0                 0.0                 0.0   
2                      0.0                 0.0                 0.0   
3                      0.0                 0.0                 0.0   
4                      0.0                 0.0                 0.0   
...                    ...                 ...                 ...   
511945                 0.0                 0.0                 0.0   
511946                 0.0                 0.0                 0.0   
511947                 0.0                 0.0                 0.0   
511948                 0.0                 0.0                 0.0   
511949                 0.0                 0.0                 0.0   

        song_popularity|18  song_popularity|19  song_popularity|20  \
0                      0.0                 0.0                 0.0   
1                      0.0                 0.0                 0.0   
2                      0.0                 0.0                 0.0   
3                      0.0                 0.0                 0.0   
4                      0.0                 0.0                 0.0   
...     

In [ ]:
def generate_playlist_recos(df, features, nonplaylist_features):
    
    non_playlist_df = df[df['song_id'].isin(nonplaylist_features['song_id'].values)]
    non_playlist_df['sim'] = cosine_similarity(nonplaylist_features.drop('song_id', axis = 1).values, features.values.reshape(1, -1))[:,0]
    non_playlist_df_top_100 = non_playlist_df.sort_values('sim',ascending = False).head(100)
    #non_playlist_df_top_10['url'] = non_playlist_df_top_10['song_id'].apply(lambda x: sp.track(x)['album']['images'][1]['url'])
    
    return non_playlist_df_top_100

In [ ]:
reco_top100 = generate_playlist_recos(spotify_complete_df, playlist_vector, non_playlist_song_vector)

In [ ]:
reco_top100

song_id  \
44124  2SWzpkGl61yQXmmvXsnnMw   
44123  3FPKjsVy2at510taiUw55R   
44122  6Uf5Zd1MRRyYkWg03iVu78   
44126  13Yqzi8EGpVUjqhGyHhkQE   
44112  37AibkNTzuQgPI5QGHYbdz   
...                       ...   
21113  6Zy82cYdN3x9ktUpQxHydk   
21128  4IClxzDjNjeuDZSdbnZKir   
21191  7eocs06QszmFJwnFwHe1GJ   
21173  58mcD0dYrT2jjngm3Y0DWh   
21152  5QDiWckG3OLuqo1M9GKFKn   

                                               song_name  \
44124          Concierto De Aranjuez: 3. Allegro Gentile   
44123      Concierto De Aranjuez: 1. Allegro Con Spirito   
44122  Fantasía para un gentilhombre for Guitar and S...   
44126                                    En los trigales   
44112  I. Allegro con spirito from Concierto de Aranj...   
...                                                  ...   
21113                    Piano Sonata in B Minor, S. 178   
21128                                 No. 7, Funérailles   
21191    Hungarian Rhapsody No.2 in C sharp minor, S.244   
21173                     Valses oubliées, S. 215, No. 1   
21152  Piano Sonata in B Minor, S. 178: II. Andante s...   

                    artist_id      artist_name  song_popularity  duration_ms  \
44124  3eqv9LW7ZXlYWXVFjHS4Mr  Joaquín Rodrigo               34       325733   
44123  3eqv9LW7ZXlYWXVFjHS4Mr  Joaquín Rodrigo               36       346160   
44122  3eqv9LW7ZXlYWXVFjHS4Mr  Joaquín Rodrigo               35       124707   
44126  3eqv9LW7ZXlYWXVFjHS4Mr  Joaquín Rodrigo                3       213200   
44112  3eqv9LW7ZXlYWXVFjHS4Mr  Joaquín Rodrigo                1       357600   
...                       ...              ...              ...          ...   
21113  1385hLNbrnbCJGokfH2ac2      Franz Liszt               15      1803280   
21128  1385hLNbrnbCJGokfH2ac2      Franz Liszt                9       630213   
21191  1385hLNbrnbCJGokfH2ac2      Franz Liszt               29       580000   
21173  1385hLNbrnbCJGokfH2ac2      Franz Liszt                0       186053   
21152  1385hLNbrnbCJGokfH2ac2      Franz Liszt               38       361960   

       explicit release_date  year  danceability  ...  speechiness  \
44124         0   1991-01-01  1991         0.546  ...       0.1540   
44123         0   1991-01-01  1991         0.576  ...       0.0400   
44122         0   1990-01-01  1990         0.689  ...       0.0630   
44126         0         1960  1960         0.423  ...       0.0557   
44112         0         1945  1945         0.535  ...       0.0337   
...         ...          ...   ...           ...  ...          ...   
21113         0         1930  1930         0.310  ...       0.0428   
21128         0         1930  1930         0.299  ...       0.0369   
21191         0   1974-01-01  1974         0.390  ...       0.0516   
21173         0         1942  1942         0.483  ...       0.0485   
21152         0         1950  1950         0.406  ...       0.0416   

       acousticness  liveness  valence    tempo  time_signature  \
44124         0.942    0.6860   0.6950  166.638               4   
44123         0.935    0.0720   0.3850  130.573               3   
44122         0.955    0.1100   0.5020  120.895               4   
44126         0.983    0.0930   0.3360  115.318               4   
44112         0.958    0.1120   0.3700  124.464               3   
...             ...       ...      ...      ...             ...   
21113         0.979    0.1620   0.0634   79.903               4   
21128         0.991    0.1640   0.0930   82.504               4   
21191         0.988    0.1130   0.0623  101.281               3   
21173         0.992    0.0745   0.0840   76.009               4   
21152         0.986    0.1430   0.0586   81.916               3   

                                    genre  artist_followers  \
44124                       ['classical']           29947.0   
44123                       ['classical']           29947.0   
44122                       ['classical']           29947.0   
44126                       ['classical']    

In [ ]:
reco_top100.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\reco_top100.csv')

### Analyzing the recommendations

In [ ]:
# 10 most prominent features of playlist vector
playlist_vector_sorted = playlist_vector.sort_values(by=['0'])
playlist_vector_sorted.tail(10)

0
1732  5.988437774316296
2625  6.073285281255938
1888  6.075011085805852
3811  6.687220578309996
8     6.756322930745469
2599  7.141657868778475
1     7.254086781029262
7                8.2816
3145  8.542709898521927
840   9.988666356656388

In [ ]:
max_features = playlist_song_vector.columns[[839, 3144, 6, 0, 2598, 7, 3810, 1887, 2624, 1731]]
max_features

Index(['genre|classic_rock', 'genre|permanent_wave', 'valence', 'danceability',
       'genre|mellow_gold', 'tempo', 'genre|soft_rock', 'genre|heartland_rock',
       'genre|metal', 'genre|glam_metal'],
      dtype='object')

In [ ]:
top_10_features = playlist_song_vector[['genre|classic_rock', 'genre|permanent_wave', 'valence', 'danceability',
       'genre|mellow_gold', 'tempo', 'genre|soft_rock', 'genre|heartland_rock',
       'genre|metal', 'genre|glam_metal']]

In [ ]:
top_10_features

genre|classic_rock  genre|permanent_wave  valence  danceability  \
0             0.384760              0.490956   0.0870      0.098890   
1             0.384760              0.490956   0.1264      0.131988   
2             0.000000              0.000000   0.1368      0.081130   
3             0.486758              0.000000   0.1820      0.108981   
4             0.510664              0.000000   0.0924      0.135419   
..                 ...                   ...      ...           ...   
62            0.000000              0.262147   0.0992      0.081130   
63            0.000000              0.262147   0.0626      0.065388   
64            0.246834              0.000000   0.1144      0.125732   
65            0.246834              0.000000   0.1930      0.154390   
66            0.246834              0.000000   0.0824      0.091019   

    genre|mellow_gold     tempo  genre|soft_rock  genre|heartland_rock  \
0            0.000000  0.091009         0.000000              0.000000   
1            0.000000  0.093226         0.000000              0.000000   
2            0.000000  0.101828         0.000000              0.000000   
3            0.000000  0.102519         0.000000              0.000000   
4            0.000000  0.092381         0.000000              0.000000   
..                ...       ...              ...                   ...   
62           0.000000  0.066406         0.000000              0.000000   
63           0.000000  0.067171         0.000000              0.000000   
64           0.258317  0.068498         0.266359              0.378284   
65           0.258317  0.092556         0.266359              0.378284   
66           0.258317  0.137944         0.266359              0.378284   

    genre|metal  genre|glam_metal  
0       0.00000               0.0  
1       0.00000               0.0  
2       0.34237               0.0  
3       0.00000               0.0  
4       0.00000               0.0  
..          ...               ...  
62      0.00000               0.0  
63      0.00000               0.0  
64      0.00000               0.0  
65      0.00000               0.0  
66      0.00000               0.0  

[67 rows x 10 columns]

In [ ]:
top_10_features.to_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\top_10_features.csv')

In [ ]:
pd.set_option('display.max_colwidth', None)

In [ ]:
reco_top100 = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Rock_80s\\reco_top100.csv')

In [ ]:
reco_top100

Unnamed: 0                 song_id  \
0       144123  71SvEDmsOwIWw1IozsZoMA   
1       172813  1MqGKtY9L5qjPi8s7gX645   
2       149886  3qYuycr2crL1C8i4RJUJC2   
3       149872  2OhL4zqGeJ1O4qLGAsCy3s   
4       144139  7elZqrBZysXba7cTLkrw05   
..         ...                     ...   
95      172518  12c1PXyghlSuNVO9GZi0DH   
96      144161  0ltUsBuPjEWhMjobZoXV4h   
97      172816  2BxuYgBSxm2UYnt4u6umpF   
98      144179  3OfNDuJMLKtNFNjSPmzlRZ   
99      133786  2Dw17OjuW3d6PscCqf6D1I   

                                            song_name               artist_id  \
0   Any Way You Want It - Live at Cobo Hall in Det...  0rvjqX7ttXeg3mTy8Xscbt   
1                                    I Can't Drive 55  1hXjTjJzZTXDZ75AclOo6N   
2                                     She's Too Tough  6IRouO5mvvfcyxtPDKMYFN   
3                              Growing up the Hardway  6IRouO5mvvfcyxtPDKMYFN   
4                                      Ask the Lonely  0rvjqX7ttXeg3mTy8Xscbt   
..                                                ...                     ...   
95                                     Rock Me Tonite  3Fz2GbraVXhcpXnoi2Oe1r   
96                                           La Do Da  0rvjqX7ttXeg3mTy8Xscbt   
97                                                Red  1hXjTjJzZTXDZ75AclOo6N   
98                Girl Can't Help It - Live Video Mix  0rvjqX7ttXeg3mTy8Xscbt   
99                                           F.I.N.E.  7Ey4PD4MYsKc5I2dolUwbH   

     artist_name  song_popularity  duration_ms  explicit release_date  year  \
0        Journey               73       201693         0         1980  1980   
1    Sammy Hagar               62       254467         0   1984-01-01  1984   
2      Foreigner               33       190640         0   1984-12-12  1984   
3      Foreigner               38       253867         0   1984-12-12  1984   
4        Journey               50       233653         0   1983-02-22  1983   
..           ...              ...          ...       ...          ...   ...   
95  Billy Squier               48       297267         0         1984  1984   
96       Journey               32       181467         0         1978  1978   
97   Sammy Hagar               28       244333         0   1977-01-01  1977   
98       Journey               34       257920         0   1986-04-21  1986   
99     Aerosmith               39       249600         0   1989-01-01  1989   

    ...  speechiness  acousticness  liveness  valence    tempo  \
0   ...       0.0488       0.00251    0.1360    0.571  138.158   
1   ...       0.0308       0.00214    0.0911    0.848  133.745   
2   ...       0.0602       0.07330    0.3830    0.539  159.579   
3   ...       0.0750       0.07120    0.2880    0.636  131.487   
4   ...       0.0382       0.24800    0.2840    0.750  128.393   
..  ...          ...           ...       ...      ...      ...   
95  ...       0.0522       0.09870    0.2390    0.673  127.360   
96  ...       0.0565       0.00762    0.2280    0.655  112.595   
97  ...       0.1210       0.02440    0.0937    0.553  162.800   
98  ...       0.1360       0.00426    0.4930    0.224  130.093   
99  ...       0.0329       0.04540    0.3580    0.601  131.737   

    time_signature                                              genre  \
0                4  ['album_rock', 'classic_rock', 'hard_rock', 'm...   
1                4  ['album_rock', 'classic_rock', 'glam_metal', '...   
2                4  ['album_rock', 'classic_rock', 'hard_rock', 'h...   
3                4  ['album_rock', 'classic_rock', 'hard_rock', 'h...   
4                4  ['album_rock', 'classic_rock', 'hard_rock', 'm...   
..             ...                                                ...   
95               4  ['album_rock', 'classic_rock', 'country_rock',...   
96               3  ['album_rock', 'classic_rock', 'hard_rock', 'm...   
97               4  ['album_rock', 'classic_rock', 'glam_metal', '...   
98               4  ['album_rock', 'classic_rock', 'ha

In [ ]:
reco_top100[['song_name', 'artist_name', 'song_popularity', 'year', 'genre', 'sim']].iloc[[1, 2, 3, 4, 5]]

song_name  artist_name  song_popularity  year  \
1        I Can't Drive 55  Sammy Hagar               62  1984   
2         She's Too Tough    Foreigner               33  1984   
3  Growing up the Hardway    Foreigner               38  1984   
4          Ask the Lonely      Journey               50  1983   
5          Tooth and Nail    Foreigner               35  1984   

                                               genre       sim  
1  ['album_rock', 'classic_rock', 'glam_metal', '...  0.745809  
2  ['album_rock', 'classic_rock', 'hard_rock', 'h...  0.745481  
3  ['album_rock', 'classic_rock', 'hard_rock', 'h...  0.744689  
4  ['album_rock', 'classic_rock', 'hard_rock', 'm...  0.743595  
5  ['album_rock', 'classic_rock', 'hard_rock', 'h...  0.742843

In [ ]:
top_10_features = pd.read_csv('C:\\Users\\romai\\OneDrive\\Documents\\Studies\\KTH\P5\\DT2470 Music Informatics\\Project\\_Data\\_Classical\\top_10_features.csv')

In [ ]:
top_10_features = top_10_features.drop(columns=["Unnamed: 0"])

In [ ]:
top10_features = pd.DataFrame({'features': top_10_features.keys()})

In [ ]:
top10_features

features
0                  acousticness
1       genre|late_romantic_era
2           genre|classical_era
3            genre|romantic_era
4                      loudness
5      genre|early_romantic_era
6                    genre|post
7                         tempo
8  genre|early_modern_classical
9     genre|russian_romanticism